In [ ]:
!pip install adversarial-robustness-toolbox
!pip install foolbox
import numpy as np
import pandas as pd
from sklearn.metrics import roc_auc_score, roc_curve, auc
from sklearn.metrics import f1_score 
# from runx.logx import logx

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import datasets, transforms

from foolbox.distances import l0, l1, l2, linf

import math
import matplotlib.pyplot as plt

from art.attacks import evasion
from art.estimators.classification import PyTorchClassifier
from art.utils import load_mnist, compute_success


from datetime import datetime 
from tqdm.notebook import tqdm 
import statistics
from math import log10

import struct
from random import randrange

import multiprocessing
import concurrent.futures
import time




3.3.3


In [ ]:

IMG_SIZE = 32
BATCH_SIZE = 1

# define transforms
# transforms.ToTensor() automatically scales the images to [0,1] range
transform = transforms.Compose([transforms.ToTensor(), transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),])
# download and create datasets
train_dataset = datasets.CIFAR10(root=f'cifar10_data', train=True, transform=transform, download=True)
valid_dataset = datasets.CIFAR10(root=f'cifar10_data', train=False, transform=transform, download=True)
# define the data loaders
train_loader = DataLoader(dataset=train_dataset, batch_size=BATCH_SIZE, shuffle=True)
valid_loader = DataLoader(dataset=valid_dataset, batch_size=BATCH_SIZE, shuffle=False)
#Class labels


    
#implementing AlexNet_Exact model
class AlexNet_Exact(nn.Module):

    def __init__(self):
        super(AlexNet_Exact, self).__init__()        

        self.relu = nn.ReLU(inplace=True)
        self.pool = nn.MaxPool2d(2, 2)

        self.conv1 = nn.Conv2d(3, 24, 3, padding=1)
        self.conv2 = nn.Conv2d(24, 96, 3, padding=1)
        self.conv3 = nn.Conv2d(96, 192, 3, padding=1)
        self.conv4 = nn.Conv2d(192, 192, 3, padding=1)
        self.conv5 = nn.Conv2d(192, 96, 3, padding=1)
                
        self.dropout = nn.Dropout()
        self.linear1 = nn.Linear(96*4*4, 1024)
        self.linear2 = nn.Linear(1024, 1024)
        self.linear3 = nn.Linear(in_features = 1024, out_features = 10)
        
        
    def forward(self, x):
        # Feature extractor

        x = self.conv1(x)
        x = self.relu(x)
        x = self.pool(x)

        x = self.conv2(x)
        x = self.relu(x)
        x = self.pool(x)

        x = self.conv3(x)
        x = self.relu(x)

        x = self.conv4(x)
        x = self.relu(x)

        x = self.conv5(x)
        x = self.relu(x)
        x = self.pool(x)
                
        x = x.view(x.size(0), 96 * 4 * 4) 
        
        x = self.dropout(x)
        x = self.linear1(x)
        x = self.relu(x)
        
        x = self.dropout(x)
        x = self.linear2(x)
        x = self.relu(x)
        
        logits = self.linear3(x)
        
        return logits


targetmodel = AlexNet_Exact()

model_path = '/content/drive/MyDrive/dataset/ALEXNET_CIFAR10.pth'
targetmodel.load_state_dict(torch.load(model_path, map_location=torch.device('cpu')))
targetmodel.eval()


  0%|          | 0/170498071 [00:00<?, ?it/s]

Extracting cifar10_data/cifar-10-python.tar.gz to cifar10_data
Files already downloaded and verified


AlexNet_Exact(
  (relu): ReLU(inplace=True)
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv1): Conv2d(3, 24, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv2): Conv2d(24, 96, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv3): Conv2d(96, 192, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv4): Conv2d(192, 192, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv5): Conv2d(192, 96, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (dropout): Dropout(p=0.5, inplace=False)
  (linear1): Linear(in_features=1536, out_features=1024, bias=True)
  (linear2): Linear(in_features=1024, out_features=1024, bias=True)
  (linear3): Linear(in_features=1024, out_features=10, bias=True)
)

In [ ]:
# Take one batch of image (100) for foolbox testing 
clean_images = []
true_labels = []
for batch_idx, (X, y_true) in enumerate(train_loader):
    if batch_idx == 500:
        break
    clean_images.append(X)
    true_labels.append(y_true)

for batch_idx, (X, y_true) in enumerate(valid_loader):
    if batch_idx == 500:
        break
    clean_images.append(X)
    true_labels.append(y_true)

print(len(clean_images), len(true_labels))

1000 1000


In [ ]:
ARTclassifier = PyTorchClassifier( 
    model=targetmodel,
    loss=nn.CrossEntropyLoss(),
    optimizer=optim.Adam(targetmodel.parameters(), lr=0.01),
    input_shape=(1, IMG_SIZE, IMG_SIZE),
    nb_classes=10,
)
ARTclassifier.model.load_state_dict(targetmodel.state_dict())
ARTclassifier.model.eval()

def prediction(x):
    x_list = x[0].tolist()
    x_sort = sorted(x_list)
    max_index = x_list.index(x_sort[-1])

    x_row_max = x.max(axis=-1)
    x_row_max = x_row_max.reshape(list(x.shape)[:-1]+[1])
    x = x - x_row_max
    x_exp = np.exp(x)
    x_exp_row_sum = x_exp.sum(axis=-1).reshape(list(x.shape)[:-1]+[1])
    softmax = x_exp / x_exp_row_sum

    return softmax, max_index#, sec_index

In [ ]:
roc_curve()

In [ ]:
L0_dist, L1_dist, L2_dist, Linf_dist = [], [], [], []
Attack = evasion.HopSkipJump(classifier=ARTclassifier, targeted =False, max_iter=50, max_eval=100)
# Attack = evasion.CarliniL2Method(classifier=ARTclassifier, batch_size = BATCH_SIZE)

mid = int(len(clean_images)/2)
member_groundtruth, non_member_groundtruth = [], []

for idx, (data, target) in enumerate(zip(clean_images, true_labels)):
  data = np.array(data)  
  logit = ARTclassifier.predict(data)
  _, pred = prediction(logit)

  if pred != target.item():
    success = 1
    data_adv = data
  else:
    data_adv = Attack.generate(x=data) 
    data_adv = np.array(data_adv) 
    success = compute_success(ARTclassifier, data, [target.item()], data_adv)

  if success == 1:
    L0_dist.append(l0(data, data_adv))
    L1_dist.append(l1(data, data_adv))
    L2_dist.append(l2(data, data_adv))
    Linf_dist.append(linf(data, data_adv))

    if idx < mid:
      member_groundtruth.append(1)
    else:
      non_member_groundtruth.append(0)


member_groundtruth = np.array(member_groundtruth)
non_member_groundtruth = np.array(non_member_groundtruth)

groundtruth = np.concatenate((member_groundtruth, non_member_groundtruth))
L0_dist = np.asarray(L0_dist)
L1_dist = np.asarray(L1_dist)
L2_dist = np.asarray(L2_dist)
Linf_dist = np.asarray(Linf_dist)

AUC_Dist, Distance = [], []

fpr_list = []
tpr_list = []
fpr, tpr, _ = roc_curve(groundtruth, L0_dist, pos_label=1, drop_intermediate=False)
L0_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, L1_dist, pos_label=1, drop_intermediate=False)
L1_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, L2_dist, pos_label=1, drop_intermediate=False)
L2_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, Linf_dist, pos_label=1, drop_intermediate=False)
Linf_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

print(f'fpr list: {fpr_list}')
print('\n')
print(f'trp list: {tpr_list}')

### AUC based on distance
auc_score = {'L0_auc':L0_auc, 'L1_auc':L1_auc, 'L2_auc':L2_auc, 'Linf_auc':Linf_auc}
AUC_Dist.append(auc_score)

### Distance of L0, L1, L2, Linf
middle= int(len(L0_dist)/2)
for idx, (l0_dist, l1_dist, l2_dist, linf_dist) in enumerate(zip(L0_dist, L1_dist, L2_dist, Linf_dist)):  
  if idx < middle:
    data = {'L0Distance':l0_dist, 'L1Distance':l1_dist, 'L2Distance':l2_dist, 'LinfDistance':linf_dist, 'Status':'Member'}
  else:
    data = {'L0Distance':l0_dist, 'L1Distance':l1_dist, 'L2Distance':l2_dist, 'LinfDistance':linf_dist, 'Status':'Non-member'}
  
  Distance.append(data)


df = pd.DataFrame()
AUC_Dist = df.append(AUC_Dist, ignore_index=True)
df = pd.DataFrame()
Distance = df.append(Distance, ignore_index=True)

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

...

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

HopSkipJump:   0%|          | 0/1 [00:00<?, ?it/s]

AttributeError: ignored

In [ ]:
path = '/content/drive/MyDrive/dataset'
for i, fpr in enumerate(fpr_list):
  np.save(f'{path}/fpr_L{i}.npy', fpr)


for i, tpr in enumerate(tpr_list):
  np.save(f'{path}/tpr_L{i}.npy', tpr)

In [ ]:
AUC_Dist, Distance = [], []

fpr_list = []
tpr_list = []
fpr, tpr, _ = roc_curve(groundtruth, L0_dist, pos_label=1, drop_intermediate=False)
L0_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, L1_dist, pos_label=1, drop_intermediate=False)
L1_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, L2_dist, pos_label=1, drop_intermediate=False)
L2_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

fpr, tpr, _ = roc_curve(groundtruth, Linf_dist, pos_label=1, drop_intermediate=False)
Linf_auc = round(auc(fpr, tpr), 4)
fpr_list.append(fpr)
tpr_list.append(tpr)

print(f'fpr list: {fpr_list}')
print('\n')
print(f'trp list: {tpr_list}')

### AUC based on distance
auc_score = {'L0_auc':L0_auc, 'L1_auc':L1_auc, 'L2_auc':L2_auc, 'Linf_auc':Linf_auc}
AUC_Dist.append(auc_score)

### Distance of L0, L1, L2, Linf
middle= int(len(L0_dist)/2)
for idx, (l0_dist, l1_dist, l2_dist, linf_dist) in enumerate(zip(L0_dist, L1_dist, L2_dist, Linf_dist)):  
  if idx < middle:
    data = {'L0Distance':l0_dist, 'L1Distance':l1_dist, 'L2Distance':l2_dist, 'LinfDistance':linf_dist, 'Status':'Member'}
  else:
    data = {'L0Distance':l0_dist, 'L1Distance':l1_dist, 'L2Distance':l2_dist, 'LinfDistance':linf_dist, 'Status':'Non-member'}
  
  Distance.append(data)


df = pd.DataFrame()
AUC_Dist = df.append(AUC_Dist, ignore_index=True)
df = pd.DataFrame()
Distance = df.append(Distance, ignore_index=True)

fpr list: [array([0.        , 0.34581498, 0.57268722, 0.66299559, 0.70704846,
       0.7246696 , 0.73788546, 0.74889868, 0.75110132, 0.75330396,
       0.75550661, 0.76431718, 0.76651982, 0.77312775, 0.77753304,
       0.77973568, 0.78634361, 0.78854626, 0.78854626, 0.79295154,
       0.79295154, 0.79515419, 0.79735683, 0.79955947, 0.80396476,
       0.80396476, 0.8061674 , 0.81057269, 0.81057269, 0.81277533,
       0.81718062, 0.81718062, 0.8215859 , 0.82378855, 0.83039648,
       0.83039648, 0.83259912, 0.83480176, 0.83700441, 0.83920705,
       0.84140969, 0.84140969, 0.84361233, 0.84361233, 0.84361233,
       0.84361233, 0.84581498, 0.84801762, 0.85022026, 0.85022026,
       0.85242291, 0.85462555, 0.85682819, 0.85682819, 0.85903084,
       0.85903084, 0.86123348, 0.86123348, 0.86123348, 0.86343612,
       0.86563877, 0.86784141, 1.        ]), array([0.        , 0.        , 0.00220264, 0.00440529, 0.00660793,
       0.00881057, 0.01101322, 0.01101322, 0.01101322, 0.01101322,
      

In [ ]:
print(AUC_Dist)


   L0_auc  L1_auc  L2_auc  Linf_auc
0  0.5966  0.6292   0.629    0.6291


In [ ]:
print(Distance)

    L0Distance   L1Distance    L2Distance   LinfDistance      Status
0     [3072.0]  [104.79558]   [2.5412323]   [0.28202018]      Member
1     [3071.0]   [57.11534]   [1.3709575]   [0.09930158]      Member
2     [3071.0]  [47.861008]   [1.1861683]   [0.10363674]      Member
3     [3072.0]  [26.705606]  [0.63876104]  [0.063928485]      Member
4     [3071.0]   [69.07071]   [1.6861801]   [0.14834447]      Member
..         ...          ...           ...            ...         ...
912   [3064.0]   [91.63319]   [2.1806219]   [0.19573605]  Non-member
913   [3071.0]  [34.943153]  [0.81631494]   [0.06651789]  Non-member
914      [0.0]        [0.0]         [0.0]          [0.0]  Non-member
915   [3071.0]  [69.091156]    [1.699884]   [0.19542629]  Non-member
916   [3071.0]  [22.971485]  [0.64102787]  [0.098269284]  Non-member

[917 rows x 5 columns]


In [ ]:
mem_dis = Distance['L0Distance'].head(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')



mem_dis = Distance['L0Distance'].tail(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Non-Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')


Member:  distortion (mean) = 3035.919921875
Non-Member:  distortion (mean) = 2696.699951171875


In [ ]:
mem_dis = Distance['L1Distance'].head(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')

mem_dis = Distance['L1Distance'].tail(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Non-Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')


Member:  distortion (mean) = 39.709999084472656
Non-Member:  distortion (mean) = 32.09000015258789


In [ ]:
mem_dis = Distance['L2Distance'].head(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Member:  distortion (mean) = {np.mean(tmp)}')

mem_dis = Distance['L2Distance'].tail(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Non-Member:  distortion (mean) = {np.mean(tmp)}')


Member:  distortion (mean) = 0.9729211330413818
Non-Member:  distortion (mean) = 0.7891587018966675


In [ ]:
mem_dis = Distance['LinfDistance'].head(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')

mem_dis = Distance['LinfDistance'].tail(500)
tmp = []
for i in mem_dis:
  tmp.append(i[0])
print(f'Non-Member:  distortion (mean) = {round(statistics.mean(tmp), 2)}')


Member:  distortion (mean) = 0.09000000357627869
Non-Member:  distortion (mean) = 0.07000000029802322
